K-means Algorithm
-----------------------

*Mirco Musolesi*

This code requires the `haversine` library, which is possible to install as follows:

In [13]:
!pip install haversine

In [16]:
# The k-means algorithm takes a dataset X of N points as input, together with a parameter K specifying how many 
# clusters to create. The output is a set of K cluster centroids and a labeling of X that assigns each of the 
# points in X to a unique cluster. All points within a cluster are closer in distance to their centroid than they 
# sare to any other centroid.

from __future__ import division
from haversine import haversine
import random

""" It is a class for clustering location data by using k-means clustering approach """
class KMeans:

    
    def __init__(self, k):
        self.k = k          # number of clusters
        self.centroids = None   # means of clusters
        

    """ Return the id of the cluster closest to the input """
    def classify(self, p):
        # taken distance with first centroid as the min_dist (minimum distance) from the given point
        min_dist = self.get_squared_distance(p, self.centroids[0]) 
        cent = 0
        # checking if any other centroid has distance (from the given point) less than min_dist
        for i in range(1, self.k):
            dist = self.get_squared_distance(p, self.centroids[i])
            if min_dist > dist:
                cent = i
        return cent

    
    def train(self, p_list):
        # randomly selecting K points as centroids
        self.centroids = random.sample(p_list, self.k)
        # this is an empty list which will store the cluster ids
        c_ids = []
        
        while True:
            # Compute new cluster ids
            new_c_ids = []
            for p in p_list:
                new_c_ids.append(self.classify(p))
            
            # If no cluster ids have changed, we're done. No need to compute the cluster ids again.
            if c_ids == new_c_ids:                
                return

            # Otherwise store the new cluster ids, update the centroids and compute new cluster ids
            c_ids = new_c_ids

            # updating the centroids (i.e. self.centroids)
            for k in range(self.k):
                # find all points in the cluster k and store them in k_points
                k_points = []
                for i in range(len(c_ids)):
                    if c_ids[i] == k:
                        k_points.append(p_list[i])
                if k_points: # this will avoid divide-by-zero error if k_points is empty
                    # compute centroid of cluster k by using points in k_points
                    self.centroids[k] = self.get_centroid(k_points) 
                
                   

    """ Computes squared distance between two points """
    def get_squared_distance(self, p1, p2):
        dist_kms = haversine(p1, p2, unit = "km") 
        return dist_kms ** 2
    
    """ Computes centroid of the given points """
    def get_centroid(self, all_points):
        lats = []
        lons = []
        # get list of all lats and lons
        for p in all_points:
            lats.append(p[0])
            lons.append(p[1])
        # compute the means of lats and lons
        c_lat = float(sum(lats))/len(lats)
        c_lon = float(sum(lons))/len(lons)
        centroid = (c_lat, c_lon)
        return centroid
    

You can invoke the class using the code below:

In [17]:
import csv

""" Fetch all points from the mobility_traces file """
data = list()
with open('./mobility_traces.csv', 'r') as f:
    reader = csv.DictReader( f )
    for line in reader:
        data.append(line)
points = [(float(d['latitude']), float(d['longitude'])) for d in data]

""" Clustering the points with K as 3 (i.e., in 3 clusters) """
K = 3
km = KMeans(K)
km.train(points) # train the model
c_ids = []
for p in points:
    c_id = km.classify(p)
    c_ids.append(c_id)

# Creating a list of K empty lists and storing points of each cluster in separate sub-lists
cp_lists = []
for k in range(0,K):
    k_list = []
    for i in range(len(points)):
        if c_ids[i] == k:
            k_list.append(points[i]) # append all points that are in cluster k
    cp_lists.append(k_list)


And you can use the following code to plot points belonging to a certain cluster with different colours using the code below:

In [19]:
""" Plotting points on the map with unique color for different clusters """
from folium import Map, Marker, Icon

# create a map with some center and zoom
km_map = Map(points[0], zoom_start=12)

# define 3 colors for 3 clusters
cols = ["red", "green", "blue"]

# create and add markers for points in each cluster. 
for i in range(K):
    for p in cp_lists[i]:
        marker = Marker(p)
        Icon(color=cols[i], icon='user').add_to(marker) # setting marker icon color based on the cluser index
        marker.add_to(km_map)

# display the map
km_map

Possible extensions (These are advanced extensions, not required for coursework and exam):
1. Implement a program that perform the $k$-means algorithm on a set of points loaded from a text file generated by you.
2. Plot the resulting clusters using the `matplotlib` library, possibly displaying points with different colours for different clusters: (http://matplotlib.org/users/pyplot_tutorial.html).
3. [VERY HARD] Implement an algorithm that automatically selects the optimal number of clusters $k$.